In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
import seaborn as sns
import os
import io
from collections import Counter
from itertools import groupby
import ipywidgets as widgets
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import pairwise_distances
from nolitsa import delay, dimension, noise, utils

upload = widgets.FileUpload(accept='.csv', multiple=True)
lag_slider = widgets.IntSlider(value=50, min=10, max=250, step=1, description='Max Lag:')
dim_slider = widgets.IntSlider(value=10, min=1, max=20, step=1, description='Max Dim:')
rp_threshold_slider = widgets.FloatSlider(value=0.30, min=0.1, max=1.0, step=0.01, description='RP Threshold:')
fnn_threshold_slider = widgets.FloatSlider(value=0.10, min=0.01, max=0.2, step=0.01, description='FNN Threshold:')
variable_names = ['x', 'y', 'z']

# -----------------------------
# Data Loading and Preprocessing
# -----------------------------

def load_and_preprocess_data(data_path):
    data = pd.read_csv(data_path, skiprows=1, usecols=[0, 1, 2], names=variable_names).dropna()
    scaler = MinMaxScaler()
    data_normalized = pd.DataFrame(scaler.fit_transform(data), columns=data.columns)
    return data_normalized

# -----------------
# Mutual Information
# -----------------

def localmin(variable):
    return (np.diff(np.sign(np.diff(variable))) > 0).nonzero()[0] + 1

def binscalc(data):
    return int(np.ceil(np.sqrt(len(data))))

def calculate_mi(data, variable_index, target_variable_index, max_lag):
        bin_size = binscalc(data)
        mi_values = np.array([delay.mi(data[:, variable_index], np.roll(data[:, target_variable_index], -lag), bins=bin_size)
                              for lag in range(1, max_lag + 1)])
        return noise.sma(mi_values, hwin=1)
        
def find_first_local_min(smoothed_mi):
    local_minima_indices = localmin(smoothed_mi)
    return (local_minima_indices + 1)[0] if local_minima_indices.size > 0 else None

def estimate_optimal_ac_delay(data):
    return np.argmax(delay.acorr(data) < 1.0 / np.e)

def estimate_optimal_delay(data, max_lag, variable_names):
    num_vars = data.shape[1]
    optimal_mi_delay_matrix = np.empty((num_vars, num_vars))
    optimal_ac_delay_matrix = np.empty(num_vars)
    mi_values_for_angles = {angle: [] for angle in variable_names}
    
    for var_index in range(num_vars):
        for target_var_index in range(num_vars):
            smoothed_mi = calculate_mi(data, var_index, target_var_index, max_lag)
            optimal_mi_delay_matrix[var_index, target_var_index] = find_first_local_min(smoothed_mi)
            if var_index == target_var_index:
                mi_values_for_angles[variable_names[var_index]] = smoothed_mi

        optimal_ac_delay_matrix[var_index] = estimate_optimal_ac_delay(data[:, var_index])
    
    return optimal_mi_delay_matrix, optimal_ac_delay_matrix, mi_values_for_angles

# --------------------------
# Embedding Dimension Estimation
# --------------------------

def estimate_embedding_dimension(data, optimal_delay, optimal_autocorrelation, max_dim, fnn_threshold):
    dimensions = np.arange(1, max_dim + 1)
    F1, F2, F3 = dimension.fnn(data, tau=optimal_delay, dim=dimensions, window=optimal_autocorrelation, metric='euclidean', maxnum = 5000)
    embedding_dimension = next((d for d, f in zip(dimensions, F1) if f < fnn_threshold), None)
    return (embedding_dimension, dimensions, F1) if embedding_dimension else ("No suitable embedding dimension found under specified thresholds.", dimensions, F1)

# -------------------------
# Phase Space Reconstruction
# -------------------------

def phase_space_reconstruction(data, embedding_dimensions, optimal_mi_delay_matrix):
    num_vars = data.shape[1]
    min_size = float('inf')
    reconstructed_data = []
    for i in range(num_vars):
        reconstructed_vector = utils.reconstruct(data[:, i], embedding_dimensions[variable_names[i]], int(optimal_mi_delay_matrix[i, i]))
        min_size = min(min_size, reconstructed_vector.shape[0])
        reconstructed_data.append(reconstructed_vector)

    truncated_data = [vec[:min_size] for vec in reconstructed_data]
    return np.concatenate(truncated_data, axis=1)

# ----------
# Plotting
# ----------

def plot_mi(mi_values_for_angles, results_folder):
    fig, ax = plt.subplots(figsize=(10, 5))
    for angle, values in mi_values_for_angles.items():
        ax.plot(values, label=f'MI for {angle}')
    ax.set_title('Mutual Information')
    ax.set_xlabel('Lag')
    ax.set_ylabel('MI')
    ax.legend()
    plt.tight_layout()
    save_plot(results_folder, 'mutual_information_plot.png')
    plt.show()


def plot_fnn(fnn_values_for_angles, dimensions, results_folder):
    fig, ax = plt.subplots(figsize=(10, 5))
    for angle, values in fnn_values_for_angles.items():
        ax.plot(dimensions, values, label=f'FNN for {angle}')
    ax.set_title('False Nearest Neighbors')
    ax.set_xlabel('Embedding Dimension')
    ax.set_ylabel('FNN')
    ax.legend()
    plt.tight_layout()
    save_plot(results_folder, 'fnn_plot.png')
    plt.show()

def plot_phase_space(data_normalized, reconstructed, embedding_dimensions, results_folder):
    variables = data_normalized.columns.tolist()
    colors = ['blue', 'green', 'red']
    
    fig = plt.figure(figsize=(20, 10))
    gs = gridspec.GridSpec(2, 4, width_ratios=[1, 1, 1, 1], height_ratios=[1, 1])
    embedding_dims_cumsum = np.cumsum([0] + [embedding_dimensions[var] for var in variables])
    
    def plot_2d(ax, data, title, xlabel, ylabel, color):
        ax.plot(*data, color=color, linewidth=0.5, label=f"{xlabel} vs {ylabel}")
        ax.set_title(title)
        ax.set_xlabel(xlabel)
        ax.set_ylabel(ylabel)
        ax.legend()
        ax.set_aspect('equal')
    
    for i, var in enumerate(variables):
        start_idx, end_idx = embedding_dims_cumsum[i:i + 2]
        ax = plt.subplot(gs[0, i])
        plot_2d(ax,
                (reconstructed[:len(data_normalized), start_idx], reconstructed[:len(data_normalized), start_idx + 1]),
                f'Phase Space Reconstruction for {var}',
                f'{var}(t)',
                f'{var}(t + delay)',
                colors[i])
    
    ax = plt.subplot(gs[0, 3], projection='3d')
    ax.plot(data_normalized[variables[0]], data_normalized[variables[1]], data_normalized[variables[2]], color='purple', linewidth=0.7)
    ax.set_title('Original 3D Phase Space')
    ax.set_xlabel('x')
    ax.set_ylabel('y')
    ax.set_zlabel('z')
    
    for i, var in enumerate(variables):
        start_idx, end_idx = embedding_dims_cumsum[i:i + 2]
        if end_idx - start_idx >= 3:
            ax = plt.subplot(gs[1, i], projection='3d')
            ax.plot(reconstructed[:, start_idx],
                    reconstructed[:, start_idx + 1],
                    reconstructed[:, start_idx + 2], color=colors[i], linewidth=0.5)
            ax.set_title(f'Reconstructed 3D Phase Space for {var}')
            ax.set_xlabel(f'{var}(t)')
            ax.set_ylabel(f'{var}(t + τ)')
            ax.set_zlabel(f'{var}(t + 2τ)')
    
    plt.tight_layout()
    save_plot(results_folder, 'phase_space_plot.png')
    plt.show()
    
def plot_recurrence_plot(rp_matrix, results_folder):
    plt.figure(figsize=(10, 10))
    plt.imshow(rp_matrix, cmap='binary', origin='lower')
    plt.title('Recurrence Plot')
    plt.xlabel('Time')
    plt.ylabel('Time')
    save_plot(results_folder, 'recurrence_plot.png')    
    plt.show()

def plot_correlation_heatmap(data_normalized, results_folder):
    correlations = data_normalized.corr()
    plt.figure(figsize=(8, 6))
    sns.heatmap(correlations, annot=True, cmap='coolwarm', vmin=-1, vmax=1)
    plt.title('Correlation Heatmap')
    save_plot(results_folder, 'correlation_heatmap.png')
    plt.show()
    
def save_plot(folder, filename):
    if not os.path.exists(folder):
        os.makedirs(folder)
    plt.savefig(os.path.join(folder, filename))
    
# ----------------------
# MdRQA Analysis
# ----------------------
    
def compute_recurrence_plot(data, rp_threshold):
    distances = pairwise_distances(data)
    return distances < rp_threshold    

def compute_histograms(M, n):
    diag_hist = np.zeros(n+1)
    vert_hist = np.zeros(n+1)

    for i in range(n):
        diag_counter = 0
        vert_counter = 0
        for j in range(n-i):
            if M[i+j][j] == 1:
                diag_counter += 1
            else:
                if diag_counter > 0:
                    diag_hist[diag_counter] += 2 
                    diag_counter = 0

            if M[j][i] == 1:
                vert_counter += 1
            else:
                if vert_counter > 0:
                    vert_hist[vert_counter] += 1
                    vert_counter = 0

        if diag_counter > 0:
            diag_hist[diag_counter] += 2
        if vert_counter > 0:
            vert_hist[vert_counter] += 1

    diag_hist[n] /= 2

    return diag_hist, vert_hist

def compute_average(hst, min_line_length, n):
    numerator = sum(i * hst[i] for i in range(min_line_length, n+1))
    denominator = sum(hst[i] for i in range(min_line_length, n+1))
    return numerator / (denominator if denominator > 0 else 1)

def compute_entropy(hst, min_line_length, n):
    total = sum(hst[min_line_length:n+1])
    if total > 0:
        return -sum((hst[i]/total) * np.log(hst[i]/total) for i in range(min_line_length, n+1) if hst[i] != 0)
    else:
        return 0

def compute_max_line_length(hst, n):
    return max((i for i in range(1, n+1) if hst[i] != 0), default=1)

def compute_rqa_measures(rp_matrix, min_line_length=2):
    n = rp_matrix.shape[0]

    diag_hist, vert_hist = compute_histograms(rp_matrix, n)

    rec = np.sum(rp_matrix) / n**2 * 100
    mean_l = compute_average(diag_hist, min_line_length, n)
    entr_l = compute_entropy(diag_hist, min_line_length, n)
    mean_v = compute_average(vert_hist, min_line_length, n)
    max_v = compute_max_line_length(vert_hist, n)
    entr_v = compute_entropy(vert_hist, min_line_length, n)

    rqa_measures =  {
        'Length of Time Series': n,
        'Percentage of Recurrent Points (%REC)': rec,
        'Avarage Diagonal Line Length (MeanL)': mean_l,
        'Diagonal Line Entropy (EntrL)': entr_l,
        'Avarage Vertical Line Length (MeanV)': mean_v,
        'Max Vertical Line Length (MaxV)': max_v,
        'Vertical Line Entropy (EntrV)': entr_v,
    }

    return rqa_measures

# ------------------------------
# Widgets and Execution
# ------------------------------
    
def execute_analysis(btn):
    MAX_LAG = lag_slider.value
    MAX_DIM = dim_slider.value
    RP_THRESHOLD = rp_threshold_slider.value
    FNN_THRESHOLD = fnn_threshold_slider.value

    if not upload.value:
        print("Please upload a valid CSV file before running the analysis.")
        return
    
    print(f"Max Lag: {MAX_LAG}")
    print(f"Max Dim: {MAX_DIM}")
    print(f"RP Threshold: {RP_THRESHOLD}")
    print(f"FNN Threshold: {FNN_THRESHOLD}")

    for file_info in upload.value:
        filename = file_info['name']
        content = file_info['content']
        print(f"Processing {filename}")
        DATA_PATH = io.BytesIO(content)
        results_folder = filename.split('.')[0] + '_results'

        data_normalized = load_and_preprocess_data(DATA_PATH)
        optimal_mi_delay_matrix, optimal_ac_delay_matrix, mi_values_for_angles = estimate_optimal_delay(data_normalized.values, MAX_LAG, variable_names)

        # Calculate and print optimal delays and embedding dimensions
        embedding_dimensions = {}
        fnn_values_for_angles = {}
        for i, var_name in enumerate(variable_names):
            if np.isnan(optimal_mi_delay_matrix[i, i]):
                print(f"Error: Failed to determine an optimal delay for {var_name} using Mutual Information.")
                return
            optimal_delay = int(optimal_mi_delay_matrix[i, i])
            optimal_autocorrelation = int(optimal_ac_delay_matrix[i])
            embedding_dimension, _, fnn_values = estimate_embedding_dimension(
                data_normalized.values[:, i], optimal_delay, optimal_autocorrelation, MAX_DIM, FNN_THRESHOLD)
            embedding_dimensions[var_name] = embedding_dimension
            fnn_values_for_angles[var_name] = fnn_values
            print(f"Optimal Delay and Embedding Dimension for {var_name}:\n"
                  f"Optimal Delay: {optimal_delay}\n"
                  f"Embedding Dimension: {embedding_dimension}\n")

        # Phase Space Reconstruction
        reconstructed = phase_space_reconstruction(
            data_normalized.values, embedding_dimensions, optimal_mi_delay_matrix
        )

        # Compute and print RQA measures
        rp_matrix = compute_recurrence_plot(reconstructed, RP_THRESHOLD)
        rqa_measures = compute_rqa_measures(rp_matrix)

        print("\nRQA measures")
        for key, value in rqa_measures.items():
            if '(%REC)' in key:
                formatted_value = f"{value:.2f}%"
            else:
                formatted_value = round(value, 2)
            print(f"{key}: {formatted_value}")

        # Mutual Information plot
        plot_mi(mi_values_for_angles, results_folder)

        # False Nearest Neighbors plot
        plot_fnn(fnn_values_for_angles, np.arange(1, MAX_DIM + 1), results_folder)

        # Phase Space Reconstruction plot
        plot_phase_space(data_normalized, reconstructed, embedding_dimensions,results_folder)

        # Recurrence Plot
        plot_recurrence_plot(rp_matrix, results_folder)

        # Correlation Heatmap plot
        plot_correlation_heatmap(data_normalized, results_folder)

        # Save measures to a CSV file
        if not os.path.exists(results_folder):
            os.makedirs(results_folder)
        measures_df = pd.DataFrame.from_dict(rqa_measures, orient='index', columns=['Value'])
        measures_df.to_csv(os.path.join(results_folder, 'measures.csv'))
    
run_analysis_button = widgets.Button(description="Run Analysis")
run_analysis_button.on_click(execute_analysis)

display_widgets = [
    upload,
    lag_slider,
    dim_slider,
    rp_threshold_slider,
    fnn_threshold_slider,
    run_analysis_button
]

for widget in display_widgets:
    display(widget)

FileUpload(value=(), accept='.csv', description='Upload', multiple=True)

IntSlider(value=50, description='Max Lag:', max=250, min=10)

IntSlider(value=10, description='Max Dim:', max=20, min=1)

FloatSlider(value=0.3, description='RP Threshold:', max=1.0, min=0.1, step=0.01)

FloatSlider(value=0.1, description='FNN Threshold:', max=0.2, min=0.01, step=0.01)

Button(description='Run Analysis', style=ButtonStyle())